In [0]:
from pyspark.sql import functions as F

# UVOD
Prvo ucitavam podatke, resavam se duplikata i onda pregledam dataset da vidim kakvi su redovi, da li imam negde neka ne slaganja, kakav je format, i ako imam neke prazne kolone, kako da ih se resim.

In [0]:
df = spark.read.table("default.game_data")
total = df.count()
distinct = df.distinct().count()
print(f"Total rows = {total}, distinct = {distinct}, duplicates = {total - distinct}")

# ukloni duplikate
df = df.dropDuplicates()
raw_df = df
print(f"Rows after dropDuplicates = {raw_df.count()}")
display(raw_df)

Total rows = 183038, distinct = 91517, duplicates = 91521
Rows after dropDuplicates = 91517


AppID Name ReleaseDate EstimatedOwners PeakCCU RequiredAge Price Discount DLCCount AboutTheGame SupportedLanguages FullAudioLanguages Reviews HeaderImage Website SupportURL SupportEmail Windows Mac Linux MetacriticScore MetacriticURL UserScore Positive Negative ScoreRank Achievements Recommendations Notes AvgPlaytimeForever AvgPlaytimeTwoWeeks MedianPlaytimeForever MedianPlaytimeTwoWeeks Developers Publishers Categories Genres Tags Screenshots Movies 1818320 いせかいあどべんちゃー Mar 1, 2022 0 - 20000 1 0 7.99 0 0 Oh my god, it looks like you've been reincarnated. But don't worry, the goddess says you can live happily in another world. But there is one thing she asks of you... Isekai Adventure is an RPG where you create your own character with a skill tree and portrait import function, and explore a different world where the map changes every time you play. Take control of the powerful cheat skills bestowed upon you by the goddesses and travel through another world! Game Features ・The map changes every time you play, so you can play as many times as you want! ・You can create your own original character with the portrait import function. ・The skill tree allows you to freely decide your character's growth path. ・Powerful cheat skills from the goddess allow you to have a novel-style adventure! ・The goddesses are cute! Travel Guide ・The world is full of unknowns, so be sure to walk around and check your surroundings. ・No road is long with good company. Let's think carefully about the members and choose. ・There are many dangerous creatures in the other world, you can't be their meal, so let's fight them back! ・The more you travel, the more powerful the dangerous creatures will become, so use the skill tree to become stronger! ・If you're going to travel far, you'll want to make sure you look stylish, too. Create your own character with the portrait import function! . Japanese Japanese null https://cdn.akamai.steamstatic.com/steam/apps/1818320/header.jpg?t=1646192657 null null oyfyby@gmail.com True False False 0 null 0 15 7 null 0 0 null 0 0 0 0 OyFyBy OyFyBy Single-player RPG;Strategy Exploration;2D Platformer;Rogue-lite;Party-Based RPG;Rogue-like;RPG;Character Customization;Strategy;Hex Grid;2D;Cute;Procedural Generation;Colorful;Fantasy;Magic;Class-Based;Resource Management;Singleplayer;Pixel Graphics;Perma Death https://cdn.akamai.steamstatic.com/steam/apps/1818320/ss_92b6679b36266c532cd57ae82c5a2525a8156455.1920x1080.jpg?t=1646192657;https://cdn.akamai.steamstatic.com/steam/apps/1818320/ss_e10efd40f0a8bce3d2e7793530687c35972cdddc.1920x1080.jpg?t=1646192657;https://cdn.akamai.steamstatic.com/steam/apps/1818320/ss_df521243fe097938f92d8e620e08b751f883f863.1920x1080.jpg?t=1646192657;https://cdn.akamai.steamstatic.com/steam/apps/1818320/ss_040b10910f11e603e3081c5bb89c089a6eedc3d5.1920x1080.jpg?t=1646192657;https://cdn.akamai.steamstatic.com/steam/apps/1818320/ss_7ff087dbc7eeb390392a36f3bc3c743d5dbcb6c9.1920x1080.jpg?t=1646192657;https://cdn.akamai.steamstatic.com/steam/apps/1818320/ss_3cb8f368df462675e74d25d2fe2097f990ff0eb3.1920x1080.jpg?t=1646192657;https://cdn.akamai.steamstatic.com/steam/apps/1818320/ss_a3e835578bc8e344dffadffff65a7b6df1e96951.1920x1080.jpg?t=1646192657;https://cdn.akamai.steamstatic.com/steam/apps/1818320/ss_cba404628b3da962e19f30a5585d6ea88550dcbf.1920x1080.jpg?t=1646192657;https://cdn.akamai.steamstatic.com/steam/apps/1818320/ss_2e7af3cebc4e7849b03fbd6ddec26d195fb73afd.1920x1080.jpg?t=1646192657;https://cdn.akamai.steamstatic.com/steam/apps/1818320/ss_5f53557d60fb600f5bb5c53c28ad4ed30ac7ad82.1920x1080.jpg?t=1646192657 http://cdn.akamai.steamstatic.com/steam/apps/256874020/movie_max.mp4?t=1644950909 541150 Vox-L Dec 12, 2016 0 - 20000 0 0 9.99 0 0 Vox-L is not a game. It's a customizable virtual reality playground. By default, Vox-L is just an infinite white terrain. There's nothing there. You can't do anything fun. Sounds boring, I know... But here are some reasons we think you'll enjoy it. Reason 1: It has free multipl

Sada vidim da je kolona UserScore prazna. To ne bi trebalo da bude tako i ja cu je popuniti tako sto cu uzeti pozitivne i negativne review-ove staviti ih na vrednosti od 0-10 kako bi imali neki vid ocena korisnika.

In [0]:
df_cast = df \
  .withColumn("Positive_int", F.expr("try_cast(Positive AS INT)")) \
  .withColumn("Negative_int", F.expr("try_cast(Negative AS INT)"))

# 2) Izbroji redove gde je try_cast vratio NULL => to su „pokvareni“ zapisi
invalid_count = df_cast.filter(
    F.col("Positive_int").isNull() | F.col("Negative_int").isNull()
).count()

print(f"Broj redova sa nevalidnim Positive/Negative: {invalid_count}")

# 3) Filtriraj samo validne i preimenuj nazad u Positive/Negative
df = (
  df_cast
    .filter(F.col("Positive_int").isNotNull() & F.col("Negative_int").isNotNull())
    .drop("Positive", "Negative")
    .withColumnRenamed("Positive_int", "Positive")
    .withColumnRenamed("Negative_int", "Negative")
)

# 4) Izračunaj novi UserScore 0–10, sa round na 2 decimale
df = df.withColumn(
    "UserScore",
    F.round(
      F.when(
        (F.col("Positive") + F.col("Negative")) > 0,
        (F.col("Positive") / (F.col("Positive") + F.col("Negative"))) * 10
      ).otherwise(0),
      2
    )
)

# 5) Pregled prvih nekoliko redova da potvrdiš:
display(df.select("AppID", "Positive", "Negative", "UserScore").limit(20))

Broj redova sa nevalidnim Positive/Negative: 25


AppID Positive Negative UserScore 1818320 15 7 6.82 541150 0 0 0.0 1986620 0 0 0.0 991740 35 37 4.86 690250 8 7 5.33 403970 1318 472 7.36 613620 22 12 6.47 711350 0 3 0.0 781130 80 21 7.92 1688010 0 0 0.0 476370 13 6 6.84 434250 1133 466 7.09 1834620 16 26 3.81 229810 295 166 6.4 1240090 2 1 6.67 1217560 3 1 7.5 879000 164 92 6.41 1622690 0 0 0.0 1706470 8 1 8.89 969250 32 2 9.41

Sada kada sam to uradio vidim da imam problem da kada imam recimo 1 review koji je pozitivan imacu ocenu 10, sto nije merodavno. Moramo uvesti neku medijanu kako bismo imali donju granicu koliko ukupno reivew-oa mora da ima kako bi uopste mogli da kazemo da je fer ocenjeno.



In [0]:
df = df.withColumn("totalReviews", F.col("Positive") + F.col("Negative"))


median_val = df.stat.approxQuantile("totalReviews", [0.5], 0.01)[0]
print(f"Median ukupnih review-ova = {median_val}")

df_filtered = df.filter(F.col("totalReviews") >= median_val)

print(f"Pre filtera: {df.count()} igara")
print(f"Nakon filtera: {df_filtered.count()} igara")

display(df_filtered.select("AppID","Name","totalReviews","Positive","Negative","UserScore").limit(20))

Median ukupnih review-ova = 7.0
Pre filtera: 91492 igara
Nakon filtera: 47780 igara


AppID Name totalReviews Positive Negative UserScore 1818320 いせかいあどべんちゃー 22 15 7 6.82 991740 Era Of Newborns 72 35 37 4.86 690250 Judge Dredd 95 15 8 7 5.33 403970 The Dwarves 1790 1318 472 7.36 613620 Hoverloop 34 22 12 6.47 781130 Creatura 101 80 21 7.92 476370 MAGATAMA Earrings 19 13 6 6.84 434250 Masked Shooters 2 1599 1133 466 7.09 1834620 The Shore VR 42 16 26 3.81 229810 A Fistful of Gun 461 295 166 6.4 879000 Comanche 256 164 92 6.41 1706470 Space to Grow 9 8 1 8.89 969250 Flynguin Station 34 32 2 9.41 314760 Direct Hit: Missile War 23 10 13 4.35 1534610 ZombiesWaves 61 27 34 4.43 1325270 Escapeworld Dilemma 51 41 10 8.04 664320 Holy Potatoes! What the Hell?! 120 60 60 5.0 934120 Monkeys & Dragons 31 20 11 6.45 208710 Colour Bind 34 24 10 7.06 1175100 单词训练营 | Word Training Camp 23 20 3 8.7

Ovime smo maltene prepolovili broj redova na pola, ali opet to nam je i bio cilj kako bismo izvukli korisne podatke. Sada cemo uporediti review-ove sa cenom, po publisher-u i developer-u. Kako bismo videli koji developer pravi najbolje igre po najboljoj ceni. Da kazemo da jurimo neki bang for the buck.

In [0]:
from pyspark.sql.functions import col

# Pretpostavljam da si do sada napravio df_filtered:
#   df_filtered = df.filter(F.col("totalReviews") >= median_val)

# 1) Pokušaj da kastuješ Price u double i proveri koliko ne može da se kastuje:
df_price = df_filtered \
  .withColumn("Price_double", F.expr("try_cast(Price AS DOUBLE)"))

bad_price_count = df_price.filter(col("Price_double").isNull()).count()
print(f"Nevalidnih Price zapisa: {bad_price_count}")

# 2) Očisti redove sa nevalidnim Price-om i zadrži samo numeric Price
df_clean = df_price \
  .filter(col("Price_double").isNotNull()) \
  .drop("Price") \
  .withColumnRenamed("Price_double", "Price")

# 3) Ako želiš, prebaci i UserScore da bude DOUBLE (ako već nije):
df = df_clean.withColumn("UserScore", col("UserScore").cast("double"))

# Sada df ima numerički Price i UserScore, spreman za dalji rad
print("Sledeća provera tipova:") 
df.printSchema()

Nevalidnih Price zapisa: 0
Sledeća provera tipova:
root
 |-- AppID: string (nullable = true)
 |-- Name: string (nullable = true)
 |-- ReleaseDate: string (nullable = true)
 |-- EstimatedOwners: string (nullable = true)
 |-- PeakCCU: string (nullable = true)
 |-- RequiredAge: string (nullable = true)
 |-- Discount: string (nullable = true)
 |-- DLCCount: string (nullable = true)
 |-- AboutTheGame: string (nullable = true)
 |-- SupportedLanguages: string (nullable = true)
 |-- FullAudioLanguages: string (nullable = true)
 |-- Reviews: string (nullable = true)
 |-- HeaderImage: string (nullable = true)
 |-- Website: string (nullable = true)
 |-- SupportURL: string (nullable = true)
 |-- SupportEmail: string (nullable = true)
 |-- Windows: string (nullable = true)
 |-- Mac: string (nullable = true)
 |-- Linux: string (nullable = true)
 |-- MetacriticScore: string (nullable = true)
 |-- MetacriticURL: string (nullable = true)
 |-- UserScore: double (nullable = true)
 |-- ScoreRank: string (

# Analiza 0: Igranje sa sparkom

Ova analiza gleda izdavače igara i meri koliko su njihove igre dobro ocenjene u odnosu na cenu ("score per euro"). Prvo razdvajamo sve izdavače, zatim gledamo da li su igre sami izdavali ili za druge developere. Izračunavamo prosečnu cenu i ocenu po izdavaču i gledamo ko ima najbolji odnos kvaliteta i cene.

Na osnovu ovoga, lako vidimo koji izdavači nude najviše za uložen novac. Ovo je korisno i za gejmere koji traže jeftine ali kvalitetne igre, ali i za izdavače da uporede svoju strategiju sa konkurencijom.



In [0]:
from pyspark.sql import functions as F
from pyspark.sql.functions import split, explode, trim, col, when, count, sum, avg

# 1) Explode publishers u zasebne redove
df_pub = (
  df
    .withColumn("Publisher", explode(split(col("Publishers"), ";")))
    .withColumn("Publisher", trim(col("Publisher")))
)

# 2) Flag koji kaže da li je publisher ujedno i jedan od developera
df_pub = df_pub.withColumn(
  "self_published",
  when(
    F.array_contains(split(col("Developers"), ";"), col("Publisher")),
    True
  ).otherwise(False)
)

# 3) Grupisanje i agregacije
pub_stats = (
  df_pub
    .groupBy("Publisher")
    .agg(
      count("*").alias("total_games"),
      sum(when(col("self_published"), 1).otherwise(0)).alias("self_published_games"),
      sum(when(~col("self_published"), 1).otherwise(0)).alias("external_games"),
      F.round(avg("Price"), 2).alias("avg_price"),
      F.round(avg("UserScore"), 2).alias("avg_score")
    )
    .withColumn(
      "score_per_euro",
      F.when(col("avg_price") > 0, F.round(col("avg_score") / col("avg_price"), 2))
      .otherwise(None)
    )
    .filter(col("total_games") >= 3)
    .orderBy(col("score_per_euro").desc())
)

display(pub_stats)


Publisher total_games self_published_games external_games avg_price avg_score score_per_euro Paradise Project 24 0 24 0.17 7.63 44.88 none 8 5 3 0.12 5.33 44.42 ToastieLabs 4 4 0 0.25 7.66 30.64 Mad Labyrinth Studios LLC 3 3 0 0.25 5.97 23.88 Triority Interactive Novels 6 6 0 0.33 7.09 21.48 Ordinary Pine Studio 3 0 3 0.49 9.72 19.84 迷糊的安安 6 1 5 0.5 9.51 19.02 FoxSox Games 3 3 0 0.53 9.29 17.53 Virtual World Arcade 4 3 1 0.5 8.6 17.2 Self Published 4 0 4 0.5 8.6 17.2 ElvGames 3 3 0 0.5 8.04 16.08 PixelMouse 3 3 0 0.49 7.7 15.71 Lazrool 5 5 0 0.6 9.38 15.63 David Mulder 5 5 0 0.4 6.22 15.55 Far Few Giants 6 0 6 0.5 7.69 15.38 GZ Storm 10 9 1 0.6 8.71 14.52 ATC Games 3 3 0 0.33 4.67 14.15 Gestmorph Games 5 5 0 0.52 7.2 13.85 Cabbibo 3 3 0 0.66 9.05 13.71 Phil Fortier 4 4 0 0.74 9.85 13.31 KomBits Game Studio 5 5 0 0.59 7.85 13.31 IR Studio 7 2 5 0.51 6.77 13.27 John Wizard 9 9 0 0.55 7.29 13.25 Angel And Demons 3 0 3 0.5 6.61 13.22 Hot Chill 4 4 0 0.49 6.45 13.16 ben lunato 5 5 0 0.59 7.76 13.15 Walter Machado 18 18 0 0.71 8.93 12.58 Pirotexnik 6 6 0 0.72 8.66 12.03 Samer Khatib (Snowconesolid Productions) 3 3 0 0.66 7.94 12.03 Planescape Game Studio 3 3 0 0.66 7.88 11.94 JOZGames 7 0 7 0.8 9.23 11.54 NukGames 10 10 0 0.69 7.93 11.49 IronEqual 3 2 1 0.66 7.44 11.27 Redaster Studio 3 3 0 0.67 7.49 11.18 L. Stotch 14 14 0 0.78 8.52 10.92 Adrian Domagalski 3 3 0 0.49 5.33 10.88 PROATIV GAMES 10 0 10 0.69 7.48 10.84 Misc.261 4 4 0 0.87 9.36 10.76 The 25th Studio 4 4 0 0.93 9.77 10.51 Doctor Entertainment AB 4 4 0 0.75 7.83 10.44 Awoker Games 3 3 0 0.82 8.27 10.09 Zloy Krot Studio 11 11 0 0.54 5.43 10.06 Performance Artist 6 6 0 0.82 8.24 10.05 MGG Studio 4 0 4 0.74 7.33 9.91 Glowstick Entertainment 3 3 0 0.83 8.22 9.9 Brewsterland Studios 7 7 0 0.71 7.02 9.89 Crew Lab 17 17 0 0.9 8.88 9.87 Red × Balloon 3 1 2 1.0 9.83 9.83 Vergiu 7 7 0 0.97 9.45 9.74 3f Interactive 3 3 0 0.84 8.08 9.62 Funny Games 6 6 0 0.66 6.34 9.61 Gabriel Jacintho Bertasso 3 3 0 0.99 9.44 9.54 Lu 3 3 0 0.94 8.96 9.53 Thedox Games 5 5 0 0.99 9.42 9.52 LR Studio 3 2 1 0.99 9.38 9.47 Hunny Bunny Studio 17 14 3 0.9 8.51 9.46 Magitech Games 4 4 0 0.79 7.38 9.34 Monkeystein Games 3 0 3 0.66 6.15 9.32 XD Games Studio 3 3 0 0.99 9.22 9.31 N J FOX 3 3 0 0.66 6.14 9.3 Nyanco Channel 8 8 0 0.97 8.98 9.26 Pocket Money Games 3 3 0 0.99 9.06 9.15 Samu 3 3 0 1.0 9.14 9.14 Object Normal 3 2 1 1.0 9.08 9.08 STuNT 7 7 0 0.86 7.74 9.0 Magnolia Art 3 3 0 0.99 8.86 8.95 Quantized Bit 5 5 0 0.79 7.07 8.95 Achpile 3 3 0 0.99 8.77 8.86 Five Percents 3 3 0 0.99 8.66 8.75 SkyOne Studios 4 4 0 1.12 9.76 8.71 Coffee Studio 9 9 0 1.07 9.18 8.58 Rocha Village Games 3 0 3 0.99 8.48 8.57 凝冰剑斩 10 10 0 1.09 9.34 8.57 Snkl Studio 29 29 0 0.88 7.52 8.55 Freedomize Studio 3 3 0 0.99 8.44 8.53 Archor Games 14 0 14 0.93 7.88 8.47 deadworld games 4 4 0 1.12 9.47 8.46 Useless Studio 3 2 1 0.99 8.34 8.42 Trident Game Studio 3 3 0 0.52 4.37 8.4 Pixizora 3 0 3 1.16 9.71 8.37 Heimo Game Studio 5 4 1 1.17 9.73 8.32 Killed Pixel Games 3 3 0 0.99 8.22 8.3 AFBIK Studio 23 17 6 0.82 6.81 8.3 Daniel Jeanneau 3 3 0 0.99 8.18 8.26 Seaborgium Entertainment 21 21 0 1.09 8.98 8.24 Chun Y. 6 6 0 0.79 6.49 8.22 LTZinc 22 22 0 0.97 7.94 8.19 Game for people 16 0 16 0.87 7.07 8.13 Inspector Studios 3 0 3 0.94 7.58 8.06 Enaayah Software Development and Services Private Limited 14 14 0 0.99 7.93 8.01 Volha 3 3 0 0.99 7.93 8.01 Telltale Games 10 10 0 1.0 7.95 7.95 Lohsoft 3 3 0 0.99 7.83 7.91 Siactro 4 4 0 1.24 9.65 7.78 Oryzhon Studios 3 2 1 0.66 5.11 7.74 LeonWaan Games 4 4 0 0.99 7.65 7.73 Quarlellle 22 22 0 0.94 7.22 7.68 Sprovieri Games 12 12 0 1.16 8.84 7.62 Quiet River 25 25 0 1.21 9.11 7.53 Pequi studios 4 0 4 1.32 9.93 7.52 KrupinskiArt 4 0 4 0.75 5.62 7.49 Cronostase 8 0 8 1.32 9.76 7.39 Tribus Games Indie 8 8 0 1.32 9.74 7.38 Anvate Games 4 4 0 1.12 8.23 7.35 Milo Games 4 0 4 1.25 9.1 7.28 Remix Games 9 8 1 1.33 9.65 7.26 Abyssal Studios 9 2 7 1.29 9.34 7.24 Sheer Studios 4 4 0 1.0 7.24 7.24 Heavy Sheep 3 3 0 1.2

Analiza 0.5: Nastavak igranja

Ova analiza razdvaja sve žanrove igara (ako ih ima više po igri) i izračunava koliko igara pripada svakom žanru, koja je prosečna korisnička ocena i koja je prosečna cena po žanru. Tako vidimo koji žanrovi su najpopularniji i najcenjeniji kod igrača, kao i koliko se u proseku plaća za igru tog žanra.

Na kraju, sortiramo žanrove po prosečnoj oceni igrača – od najboljih prema slabije ocenjenim. Ovo može pomoći i developerima da vide šta igrači najviše vole, ali i kupcima koji traže igre određenog žanra sa najboljim ocenama.

In [0]:
# 1) Explode-uj semikolon-deljene žanrove u zasebne redove
df_genre = (
    df
      .withColumn("Genre", explode(split(col("Genres"), ";")))
      .withColumn("Genre", trim(col("Genre")))
)

# 2) Grupisanje i agregacije
df_genre_stats = (
    df_genre
      .groupBy("Genre")
      .agg(
         count("*").alias("num_games"),              # koliko igara po žanru
         avg("UserScore").alias("avg_user_score"),   # prosečna ocena (0–10)
         avg("Price").alias("avg_price")             # prosečna cena
      )
      .filter(col("num_games") >= 5)                # opcionalno: barem 5 igara da bi statistika bila relevantna
      .orderBy(col("avg_user_score").desc())       # sortiraj od najboljeg žanra naviše
)

display(df_genre_stats)

Genre num_games avg_user_score avg_price Casual 17805 7.68900365065992 6.0741477113169084 Indie 33972 7.656675497468488 7.289073060167667 Game Development 120 7.65575 25.526333333333337 Adventure 19249 7.651744506208108 8.965257935477336 Photo Editing 76 7.582763157894736 23.65144736842106 RPG 8884 7.578994822152186 10.296983340837327 Action 20282 7.513293560792814 8.821242481017853 Early Access 5438 7.467927546892245 10.033177638837698 Web Publishing 76 7.463157894736843 21.182236842105265 Strategy 9669 7.423428482780017 9.438344192780917 Design & Illustration 320 7.38228125 20.316875000000003 Sports 2272 7.326668133802818 10.442922535211226 Free to Play 3343 7.275411307209093 0.2667005683517798 Education 193 7.2586528497409315 12.70072538860104 Racing 1796 7.253151447661472 9.375111358574605 Simulation 10092 7.245600475624256 9.796893579072394 Animation & Modeling 264 7.204545454545454 20.957916666666673 Utilities 494 7.195971659919028 11.641234817813768 Software Training 113 7.07716814159292 17.891327433628323 Audio Production 130 7.010769230769231 21.324692307692313 Video Production 164 6.932378048780488 22.527378048780488 Sexual Content 93 6.73720430107527 5.590322580645161 Massively Multiplayer 1402 6.452845934379459 5.2333594864479345 Nudity 111 6.407027027027026 5.873513513513513 Gore 248 6.070483870967742 5.3650806451612905 Violent 414 5.848381642512077 5.355772946859907 Accounting 10 5.794999999999999 5.495

# Analaiza 1: Pearsonova korelacija
# 
Radim Pearsonovu korelaciju između Price i UserScore. Zbog vecnog pitanja da li "dobre" igre moraju da imaju visoku cenu. Ukoliko je vrednost blizu broja 1 znaci da ova cinjenica jeste tacna, a ukoliko je -1 znaci da je netacna. Vrednosti najblize 0 znaci da nema linearne veze.
Rezulat koji dobijamo je 0.0822, sto znaci da ne postoji znacajna linearna veza izmedju cene igre i prosecne ocene korisnika, odnosno skupe igre nisu nuzno i bolje ocenjene, niti jeftine nužno losije.
Cena sama po sebi nije dobar indikator kvaliteta igre (po korisnickom rejtingu)



In [0]:
from pyspark.sql import functions as F
from pyspark.sql.types import DoubleType

# 1) Castovanje cene u Double
df = df.withColumn("Price", F.col("Price").cast(DoubleType()))

# 2) Izračunavanje Pearson korelacije
corr = df.stat.corr("UserScore", "Price")
print(f"Pearsonovo_corr(Price, UserScore) = {corr:.4f}")


Pearsonovo_corr(Price, UserScore) = 0.0822


# Analiza 2 Linux i igrice?
# 
Linux sistemi postaju sve poplularniji zbog toga sto je sistem open source-a, privatniji i kada se koristi kako treba bolje optimizovan, mada populatnosti pomaze i Microsoft-ove pretnje privatnosti i generalno losa optimizacija. Zbog toga gejmeri su krenuli da se prebacuju na linux. Ideja mi je da kroz ove podatke nadjem prekretnicu, odnosno od kog trenutka u vremenu je krenula ekpsanzija linux podrzanih igara.

Iz rezultat vidimo da je na osnovu agregacije po godinama i izračunavanja apsolutnog godisnjeg rasta broja igara koje podrzavaju Linux tvrdili smo da je prekretnica pala na: 2015\. godinu. kada se broj Linux igara povecao za 351. Procenat igara koje su te godine podrzavali linux bio je 30 posto.


In [0]:
spark.conf.set("spark.sql.ansi.enabled", "false")


from pyspark.sql import functions as F
from pyspark.sql.functions import year, col, desc
from pyspark.sql.window import Window

parsed_df = (
    raw_df
    .withColumn(
        "parsed_dt",
        coalesce(
            to_date(col("ReleaseDate"), "MMM d, yyyy"),   # npr. "Apr 19, 2018"
            to_date(col("ReleaseDate"), "MMM yyyy")       # npr. "Dec 2024"
        )
    )
    # odbaci sve gde nije uspelo parsiranje
    .filter(col("parsed_dt").isNotNull())
    # izbriši originalnu kolonu i preimenuj parsed_dt
    .drop("ReleaseDate")
    .withColumnRenamed("parsed_dt", "ReleaseDate")
)


# 1) Agregacija po godini
yearly = (
    parsed_df
    .withColumn("year", year(col("ReleaseDate")))
    .groupBy("year")
    .agg(
        F.count("*").alias("total_games"),
        F.sum(F.when(col("Linux") == "True", 1).otherwise(0))
         .alias("linux_games")
    )
    .withColumn(
        "linux_pct",
        F.round(col("linux_games") / col("total_games") * 100, 2)
    )
    .orderBy("year")
)

# 2) Dodajemo YoY kolone (godišnji rast u apsolutnom broju Linux igara)
w = Window.orderBy("year")
yearly = (
    yearly
    .withColumn("prev_linux_games", F.lag("linux_games").over(w))
    .withColumn("yoy_linux_growth", col("linux_games") - col("prev_linux_games"))
)

# 3) Prikaži
display(yearly)


inflection_row = (
    yearly
    .filter(col("prev_linux_games").isNotNull())   # preskoči prvu godinu koja nema prethodnu
    .orderBy(desc("yoy_linux_growth"))
    .limit(1)
    .collect()[0]
)

year_inflect   = inflection_row["year"]
growth_inflect = inflection_row["yoy_linux_growth"]

# 5) Ispiši zaključak
print(
    f"Prekretnica u ekspanziji Linux-igara je {year_inflect}. godina, "
    f"kad je broj Linux-igara porastao za {growth_inflect} naslova u odnosu na {year_inflect - 1}. godinu."
)


/databricks/python/lib/python3.11/site-packages/pyspark/sql/connect/expressions.py:1017: UserWarning: WARN WindowExpression: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
  warnings.warn(


year total_games linux_games linux_pct prev_linux_games yoy_linux_growth 1997 2 1 50.0 null null 1998 1 1 100.0 1 0 1999 3 2 66.67 1 1 2000 2 2 100.0 2 0 2001 4 2 50.0 2 0 2002 1 0 0.0 2 -2 2003 3 1 33.33 0 1 2004 7 6 85.71 1 5 2005 7 2 28.57 6 -4 2006 69 10 14.49 2 8 2007 109 5 4.59 10 -5 2008 176 6 3.41 5 1 2009 343 28 8.16 6 22 2010 309 64 20.71 28 36 2011 286 54 18.88 64 -10 2012 356 96 26.97 54 42 2013 492 188 38.21 96 92 2014 1634 479 29.31 188 291 2015 2693 830 30.82 479 351 2016 4416 1051 23.8 830 221 2017 6334 1162 18.35 1051 111 2018 8183 1216 14.86 1162 54 2019 7827 940 12.01 1216 -276 2020 9646 1095 11.35 940 155 2021 12392 1215 9.8 1095 120 2022 13944 1299 9.32 1215 84 2023 15235 1338 8.78 1299 39 2024 7024 605 8.61 1338 -733 2025 1 0 0.0 605 -605

Prekretnica u ekspanziji Linux-igara je 2015. godina, kad je broj Linux-igara porastao za 351 naslova u odnosu na 2014. godinu.


# Analiza 3: K-Means klasterovanje

Uzimam primer sa vezbi kao ideju za analizu podataka. Vrsim segmentaciju igara u 4 tipa:
1. Klaster 0: niske cene, niski pullaytime, visoki UserScore
2. Klaster 1: skupi naslovi sa dugim prosekom igranja
3. Klaster 2: besplatne igre sa velikim brojem igrača
4. Klaster 3: mid-range igre sa umerenim ocenama

Centri klastera mi govere koje metrike kombinuju te tipove igara.
Velicine klastera pokazuju u kojoj meri je svaki segment zastupljen. 
Prosecne vrednosti po klasteru daju uvid u to sta je karakteristicno za svaki tip.

Rezultat:

Dve vrste “popularnih” besplatnih naslova (klaster 1):

Igru ne moramo naplacivati da bi imali milionske sati igranja. Ove igre su bazirane na F2P modelu sa masovnim pozitivnim review-ovima. 

Placene igre sa stvarnim ocenama (klaster 0):
Sa cenom oko $7, dobijate igre koje korisnici zaista ocenjuju 

Ovo su najverovatnije indie ili mid-tier naslovi sa jasnim feedback-om.

Segementacija novijih/neosjećivanih naslova (klasteri 2 i 3):

Igre koje kostaju izmedju $16 i $43, a jos nemaju UserScore (ocenjivanja).

Verovatno su upravo izašle ili tek skupljaju ocenama treba pratiti njihov razvoj i eventualno motivisati korisnike na review.

In [0]:
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.clustering import KMeans
import matplotlib.pyplot as plt

# 1) Odabir numeričkih kolona i čišćenje
numeric_columns = ["Price", "UserScore", "AvgPlaytimeForever", "PeakCCU", "Positive", "Negative"]
df_clean = raw_df.select(numeric_columns).na.drop()

# 2) Spoji ih u feature-vektor
assembler = VectorAssembler(inputCols=numeric_columns, outputCol="features")
data = assembler.transform(df_clean)

# 3) Treniranje K-Means modela (ovde 4 klastera, može se menjati)
kmeans = KMeans(k=4, seed=42, featuresCol="features", predictionCol="cluster")
model = kmeans.fit(data)

# 4) Dodaj oznake klastera nazad u DataFrame
clustered = model.transform(data)

# 5) Ispiši centre klastera
print("Centri klastera:")
for idx, center in enumerate(model.clusterCenters()):
    print(f"  Klaster {idx}: {center}")

# 6) Vizualizacija na prva dva feature-a (Price vs UserScore)
clustered_pd = clustered.select("features", "cluster").toPandas()

plt.figure(figsize=(8, 6))
for cluster_id in sorted(clustered_pd["cluster"].unique()):
    pts = clustered_pd[clustered_pd["cluster"] == cluster_id]
    plt.scatter(
        pts["features"].apply(lambda v: v[0]),  # standardized Price
        pts["features"].apply(lambda v: v[1]),  # standardized UserScore
        label=f"Klaster {cluster_id}",
        alpha=0.6
    )

plt.xlabel("Price (prva komponenta)")
plt.ylabel("UserScore (druga komponenta)")
plt.title("KMeans klasterovanje igara")
plt.legend()
plt.grid(True)
plt.show()


---------------------------------------------------------------------------
Py4JError                                 Traceback (most recent call last)
File <command-8459793838555326>, line 10
      7 df_clean = raw_df.select(numeric_columns).na.drop()
      9 # 2) Spoji ih u feature-vektor
---> 10 assembler = VectorAssembler(inputCols=numeric_columns, outputCol="features")
     11 data = assembler.transform(df_clean)
     13 # 3) Treniranje K-Means modela (ovde 4 klastera, može se menjati)

File /databricks/python/lib/python3.11/site-packages/pyspark/__init__.py:120, in keyword_only.<locals>.wrapper(self, *args, **kwargs)
    118     raise TypeError("Method %s forces keyword arguments." % func.__name__)
    119 self._input_kwargs = kwargs
--> 120 return func(self, **kwargs)

File /databricks/python/lib/python3.11/site-packages/pyspark/ml/feature.py:5364, in VectorAssembler.__init__(self, inputCols, outputCol, handleInvalid)
   5360 """
   5361 __init__(self, \\*, inputCols=None, outpu

# Analiza 4: Popularnosti zanrova kroz vreme
# 
Video igre se stalno menjaju. Tehnologija napreduje, a sa njom napreduju i trendovi u dizajnu, zanrovima i vrstama igara (kategorijama). Pored tehnologije, na video igre uticu i kultoroloski aspekti – bilo da je to izlazak nekog veoma popularnog filma, politicka desavanja, ili promena društvenih navika, sve to ostavlja trag na popularnosti odredjenih tipova igara.

Cilj ove analize je da otkrijemo koji su zanrovi i koje su kategorije (tipovi igranja, kao sto su single-player ili multi-player) bili najzastupljeniji u odredjenim periodima, odnosno kako su se ukusi i trendovi na trzistu video igara razvijali kroz decenije. Analizom cemo moci da prepoznamo koje su kategorije i zanrovi dominirali u razlicitim dekadama, kako dolazi do pojave novih trendova i opadanja popularnosti starih, kao i kakav je “zivotni ciklus” najvaznijih zanrova i tipova igranja.

Ovakva analiza je znacajna za izdavace, developere i analiticare industrije igara jer daje uvid u to sta je publika volela kroz vreme, ali i za razumevanje evolucije gaming kulture generalno.

Rezulat:
Iako je single-player ostao stalna kategorija kroz sve dekade, zanrovi su evoluirali od cistih akcija ka raznovrsnijoj ponudi gde indie dominira u poslednjoj deceniji. Ovaj prelaz odrazava tehnoloski razvoj, promenu distribucije i ocekivanja igrača za sve personalizovanijim i inovativnijim iskustvima.


In [0]:
from pyspark.sql import functions as F
from pyspark.sql.window import Window

# 1. Parsiraj datum i dekadu
df = (
    raw_df
    .withColumn("ReleaseDate_parsed",
        F.coalesce(
            F.to_date("ReleaseDate", "MMM d, yyyy"),
            F.to_date("ReleaseDate", "MMM yyyy")
        )
    )
    .filter(F.col("ReleaseDate_parsed").isNotNull())
    .withColumn("year", F.year("ReleaseDate_parsed"))
    .withColumn("decade", (F.col("year") / 10).cast("int") * 10)
)

# 2. Ekstrakcija kategorija (explode) po deceniji
cat = (
    df
    .withColumn("category", F.explode(F.split(F.col("Categories"), ";")))
    .withColumn("category", F.trim(F.lower(F.col("category"))))
    .filter(F.col("category") != "")
)

cat_stats = (
    cat.groupBy("decade", "category")
       .count()
       .withColumn("total_decade", F.sum("count").over(Window.partitionBy("decade")))
       .withColumn("category_pct", F.round(100 * F.col("count") / F.col("total_decade"), 2))
)

# Izaberi top kategoriju (može biti više, ako su izjednačene)
w_cat = Window.partitionBy("decade").orderBy(F.desc("count"))
cat_stats = cat_stats.withColumn("cat_rank", F.rank().over(w_cat))
top_cat = cat_stats.filter(F.col("cat_rank") == 1)

# 3. Ekstrakcija žanrova (explode) po deceniji
genre = (
    df
    .withColumn("genre", F.explode(F.split(F.col("Genres"), ";")))
    .withColumn("genre", F.trim(F.lower(F.col("genre"))))
    .filter(F.col("genre") != "")
)

genre_stats = (
    genre.groupBy("decade", "genre")
         .count()
         .withColumn("total_decade", F.sum("count").over(Window.partitionBy("decade")))
         .withColumn("genre_pct", F.round(100 * F.col("count") / F.col("total_decade"), 2))
)

w_genre = Window.partitionBy("decade").orderBy(F.desc("count"))
genre_stats = genre_stats.withColumn("genre_rank", F.rank().over(w_genre))
top_genre = genre_stats.filter(F.col("genre_rank") == 1)

# 4. Spajanje rezultata po deceniji (može biti više redova po deceniji ako ima izjednačenih)
final = (
    top_cat.join(top_genre, "decade")
           .select(
               "decade",
               "category", "category_pct",
               "genre", "genre_pct"
           )
           .orderBy("decade")
)

display(final)


decade category category_pct genre genre_pct 1990 single-player 18.52 action 60.0 2000 single-player 39.17 action 27.21 2010 single-player 25.13 indie 25.46 2020 single-player 32.28 indie 23.82

# Analiza 5: Elasticnost u potraznji
# 

Cenovna strategija u industriji video igara ima ogroman uticaj na uspeh proizvoda, ali taj uticaj nije uvek jednostavan i univerzalan za sve zanrove. Razliciti zanrovi i tipovi igara privlace razlicite tipove igraca – neko ce lako dati vise novca za AAA akciju ili RPG, dok ce kod manjih ili edukativnih igara igraci biti osetljiviji na cenu. Razumevanje elasticnosti potraznje – odnosno, koliko se broj igraca menja kada se promeni cena – moze pomoci izdavacima i developerima da pametnije pozicioniraju svoje igre na trzistu, povecaju prihode ili sirinu korisnicke baze. Ova analiza istrazuje kako elasticnost zavisi od zanra igre, sto je kljucno pitanje za efikasno upravljanje cenama, popustima i promotivnim kampanjama.

Rezulat:
Analiza elasticnosti potraznje pokazuje da ne reaguju svi zanrovi igara isto na promenu cene. Kod edukativnih, softverskih i kreativnih igara vidimo da niza cena moze privuci vise igraca, ali efekat nije drasticno izrazen. Sa druge strane, kod „mainstream“ zanrova kao sto su akcija, strategija i RPG, igre sa visom cenom najcesce imaju i veci broj igraca, sto znaci da igraci cesto vezuju cenu za kvalitet i reputaciju brenda. Ovakvi rezultati pokazuju da bi developeri i izdavaci trebalo da koriste razlicite cenovne strategije za razlicite zanrove: agresivne promocije za nišne i specijalizovane igre, dok za popularne zanrove mogu da se oslone na premium cene. Prava kombinacija moze povecati i zaradu i zadovoljstvo korisnika, dok ignorisanje ovih razlika nosi rizik gubitka potencijalne publike ili novca.

In [0]:
from pyspark.sql import functions as F
from pyspark.sql.types import DoubleType

# 1) Map owner-ranges to midpoints
def owners_midpoint(range_str):
    try:
        lo, hi = [float(x.replace(",", "")) for x in range_str.split(" - ")]
        return (lo + hi) / 2.0
    except:
        return None

mid_udf = F.udf(owners_midpoint, DoubleType())

df_elastic = (
    raw_df
      .withColumn("PriceD", F.col("Price").cast("double"))
      .withColumn("OwnersMid", mid_udf(F.col("EstimatedOwners")))
      .filter(F.col("PriceD").isNotNull() & F.col("OwnersMid").isNotNull())
      .withColumn("log_price",  F.log(F.col("PriceD")))
      .withColumn("log_owners", F.log(F.col("OwnersMid")))
)

# 2) Overall elasticity
elasticity = df_elastic.stat.corr("log_price", "log_owners")
print(f"Estimated price elasticity of demand = {elasticity:.2f}")

# 3) By-genre elasticity, dropping nulls
genre_elastic = (
    df_elastic
      .withColumn("genre", F.explode(F.split(F.col("Genres"), ";")))
      .groupBy("genre")
      .agg(F.expr("corr(log_price, log_owners)").alias("elasticity"))
      .filter(F.col("elasticity").isNotNull())       # <<— drop null rows
      .orderBy(F.col("elasticity").asc())            # most elastic (most negative) first
)

display(genre_elastic)


Estimated price elasticity of demand = 0.35


genre elasticity Animation & Modeling -0.09203396557567635 Design & Illustration -0.08617033229096752 Violent -0.08579036976983492 Photo Editing -0.08438560574986002 Gore -0.08130864213588751 Software Training -0.045302710236356014 Utilities -0.022761612894481347 Nudity -0.013513046066279963 Game Development 0.002781840002115696 Video Production 0.030046625179143114 Education 0.04205253053150712 Web Publishing 0.042311368059373744 Audio Production 0.04319745229722088 Casual 0.05218012456745903 Free to Play 0.0629532621092796 Accounting 0.11170315118607684 Indie 0.1489760610692772 Sexual Content 0.16388607621265988 Adventure 0.1821406523507987 Early Access 0.19231058911313856 Sports 0.19310897502327246 Massively Multiplayer 0.2118236345711921 Simulation 0.21228571576147084 RPG 0.2228685991319185 Racing 0.22495891121299633 Strategy 0.23312639038406752 Action 0.23633132196967502